In [1]:
import pandas as pd
import json

In [2]:
checksums = pd.read_csv("../metadata/deduplication/Jiggins_Zenodo_Img_Master_3477891Patch_checksums.csv", low_memory=False)
checksums.shape

(42143, 3)

In [3]:
ERROR_PATH = "../metadata/deduplication/Jiggins_Zenodo_Img_Master_3477891Patch_error_log_(readable).json"
with open(ERROR_PATH, "r") as error_file:
    errors = json.loads(error_file.read())
errors[:5]

[{'Image': 'Heliconius melpomene ssp. plesseni x malleti/5213_CAM017505_v.JPG',
  'file_url': 'https://zenodo.org/record/3082688/files/CAM017505_v.JPG',
  'record_number': '3082688',
  'dataset': 'Patricio Salazar',
  'CAMID': 'CAM017505',
  'Response_status': '404'},
 {'Image': 'Heliconius erato ssp. notabilis x lativitta/5450_CAM017693_d.JPG',
  'file_url': 'https://zenodo.org/record/3082688/files/CAM017693_d.JPG',
  'record_number': '3082688',
  'dataset': 'Patricio Salazar',
  'CAMID': 'CAM017693',
  'Response_status': '404'},
 {'Image': 'Heliconius erato ssp. notabilis x lativitta/5589_CAM017821_d.JPG',
  'file_url': 'https://zenodo.org/record/3082688/files/CAM017821_d.JPG',
  'record_number': '3082688',
  'dataset': 'Patricio Salazar',
  'CAMID': 'CAM017821',
  'Response_status': '404'},
 {'Image': 'Heliconius melpomene ssp. plesseni x malleti/16983_CAM017932_v_whitestandard.JPG',
  'file_url': 'https://zenodo.org/record/1748277/files/CAM017932_v_whitestandard.JPG',
  'record_num

In [4]:
error_df = pd.DataFrame(data = errors)
error_df.head()

Image  \
0  Heliconius melpomene ssp. plesseni x malleti/5...   
1  Heliconius erato ssp. notabilis x lativitta/54...   
2  Heliconius erato ssp. notabilis x lativitta/55...   
3  Heliconius melpomene ssp. plesseni x malleti/1...   
4  Heliconius melpomene ssp. plesseni x malleti/1...   

                                            file_url record_number  \
0  https://zenodo.org/record/3082688/files/CAM017...       3082688   
1  https://zenodo.org/record/3082688/files/CAM017...       3082688   
2  https://zenodo.org/record/3082688/files/CAM017...       3082688   
3  https://zenodo.org/record/1748277/files/CAM017...       1748277   
4  https://zenodo.org/record/1748277/files/CAM017...       1748277   

            dataset      CAMID Response_status  
0  Patricio Salazar  CAM017505             404  
1  Patricio Salazar  CAM017693             404  
2  Patricio Salazar  CAM017821             404  
3  Patricio Salazar  CAM017932             404  
4  Patricio Salazar  CAM017971             404

In [5]:
error_df.nunique()

Image              2666
file_url           2666
record_number         7
dataset               3
CAMID               612
Response_status       1
dtype: int64

These are all 404 Errors concentrated in 7 Records.

In [6]:
error_df.shape

(2725, 6)

We have some duplicated from the earlier round (we had 59 recorded in `second_Jiggins_Zenodo_Img_Master_3477891Patch_error_log.csv`); the way the download script was written it didn't ignore previous errors when we had to restart it, so let's check on the duplicated full entries before looking at full numbers (though 2666 is the full number of failed URLs).

Our total number of expected images is 44809, so when we remove the errors (2666), we'd exepct 42143 images, which is the count in our image folder (measured in `checksums`).

In [7]:
error_df["dupe_errors"] = error_df.duplicated(subset = list(error_df.columns), keep = "first")

error_df = error_df.loc[~error_df["dupe_errors"]]
error_df = error_df[list(error_df.columns)[:-1]]
error_df.nunique()

Image              2666
file_url           2666
record_number         7
dataset               3
CAMID               612
Response_status       1
dtype: int64

In [8]:
error_df.shape

(2666, 6)

In [9]:
error_df.record_number.value_counts()

record_number
4287444    2600
4289223      47
4288250       7
5561246       6
3082688       3
1748277       2
2813153       1
Name: count, dtype: int64

404 errors are concentrated in [record 42389223](https://zenodo.org/records/4289223) and [record 4287444](https://zenodo.org/records/4287444).

In [10]:
error_df.loc[error_df["record_number"] == "4289223"].sample(5)

Image  \
50  Heliconius timareta ssp. timareta/15017_CAM028...   
42  Heliconius melpomene ssp. malleti/15009_CAM028...   
37  Heliconius melpomene ssp. malleti/15003_CAM028...   
51  Heliconius timareta ssp. timareta/15016_CAM028...   
8   Heliconius melpomene ssp. malleti/14974_CAM028...   

                                             file_url record_number  \
50  https://zenodo.org/record/4289223/files/CAM028...       4289223   
42  https://zenodo.org/record/4289223/files/CAM028...       4289223   
37  https://zenodo.org/record/4289223/files/CAM028...       4289223   
51  https://zenodo.org/record/4289223/files/CAM028...       4289223   
8   https://zenodo.org/record/4289223/files/CAM028...       4289223   

                 dataset      CAMID Response_status  
50  Cambridge Collection  CAM028523             404  
42  Cambridge Collection  CAM028519             404  
37  Cambridge Collection  CAM028516             404  
51  Cambridge Collection  CAM028523             404  
8   Cambridge Collection  CAM028502             404

In [11]:
error_df.loc[error_df["record_number"] == "4289223"].nunique()

Image              47
file_url           47
record_number       1
dataset             1
CAMID              23
Response_status     1
dtype: int64

In [12]:
error_df.loc[error_df["record_number"] == "4289223", "Image"].values[0]

'Heliconius melpomene ssp. malleti/14972_CAM028501v.JPG'

In [13]:
error_df.loc[error_df["record_number"] == "4289223", "CAMID"].unique()

array(['CAM028501', 'CAM028502', 'CAM028503', 'CAM028504', 'CAM028505',
       'CAM028506', 'CAM028507', 'CAM028508', 'CAM028509', 'CAM028510',
       'CAM028511', 'CAM028512', 'CAM028513', 'CAM028514', 'CAM028515',
       'CAM028516', 'CAM028517', 'CAM028518', 'CAM028519', 'CAM028520',
       'CAM028521', 'CAM028522', 'CAM028523'], dtype=object)

It seems like these might be from [0.2.rachel.blow.mel.tim.ikiam.csv](https://zenodo.org/records/4289223/files/0.2.rachel.blow.mel.tim.ikiam.csv?download=1).

In [14]:
error_df.loc[error_df["record_number"] == "4287444"].sample(5)

Image  \
880            Eunica pusilla/32902_CAM044045_v.JPG   
1184      Caligo eurilochus/33209_CAM044119_fwv.CR2   
974         Pyrrhogyra edocia/32997_CAM044071_v.CR2   
1659             Memphis mora/33722_CAM044260_v.JPG   
1845  Archaeoprepona demophon/33909_CAM044311_v.CR2   

                                               file_url record_number  \
880   https://zenodo.org/record/4287444/files/CAM044...       4287444   
1184  https://zenodo.org/record/4287444/files/CAM044...       4287444   
974   https://zenodo.org/record/4287444/files/CAM044...       4287444   
1659  https://zenodo.org/record/4287444/files/CAM044...       4287444   
1845  https://zenodo.org/record/4287444/files/CAM044...       4287444   

                                                dataset      CAMID  \
880                                                 NaN  CAM044045   
1184                                                NaN  CAM044119   
974                                                 NaN  CAM044071   
1659  Heliconiine Butterfly Collection Records from ...  CAM044260   
1845  Heliconiine Butterfly Collection Records from ...  CAM044311   

     Response_status  
880              404  
1184             404  
974              404  
1659             404  
1845             404

We have some RAW files in this record (likely each has a raw and a jpg version). This is the vast majority of our 404s.

These don't see to actaully be in the [record](https://zenodo.org/records/4287444) though.

In [15]:
error_df.loc[error_df["record_number"] == "4287444"].nunique()

Image              2600
file_url           2600
record_number         1
dataset               1
CAMID               579
Response_status       1
dtype: int64

Is it possible some of these were recorded as part of this "batch 2" but are actually from batch 1 and that's why they're not there? 

Let's check the meta file: `batch2.Peru.image.names.Zenodo.xlsx`. This was opened in Numbers and exported to CSV first (using default `pd.read_excel` parameters resulted in an error trying to open the original Excel file), also dropped `Zenodo` from the filename.

In [10]:
rec_4287444 = pd.read_csv("../metadata/deduplication/Zenodo_meta_files/batch2.Peru.image.names.csv", low_memory = True)
rec_4287444.head()

File name         ID     Side  Unnamed: 3  Unnamed: 4
0  CAM043500_d.CR2  CAM043500   dorsal         NaN         NaN
1  CAM043500_d.JPG  CAM043500   dorsal         NaN         NaN
2  CAM043500_v.CR2  CAM043500  ventral         NaN         NaN
3  CAM043500_v.JPG  CAM043500  ventral         NaN         NaN
4  CAM043502_d.CR2  CAM043502   dorsal         NaN         NaN

In [11]:
rec_4287444 = rec_4287444[list(rec_4287444.columns)[:3]]
print(rec_4287444.info(show_counts=True))
rec_4287444.nunique()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3924 entries, 0 to 3923
Data columns (total 3 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   File name  3924 non-null   object
 1   ID         3924 non-null   object
 2   Side       3924 non-null   object
dtypes: object(3)
memory usage: 92.1+ KB
None


File name    3924
ID            880
Side            6
dtype: int64

In [20]:
rec_4287444.loc[rec_4287444["ID"] == "CAM044260"]

File name         ID     Side
2848  CAM044260_d.CR2  CAM044260   dorsal
2849  CAM044260_d.JPG  CAM044260   dorsal
2850  CAM044260_v.CR2  CAM044260  ventral
2851  CAM044260_v.JPG  CAM044260  ventral

Clear check that `CAM044260_v.JPG` exists as a file in the metadata, but it isn't actually in the files of the Zenodo record.

In [21]:
checksums.head()

filepath               filename  \
0  images/Eresia eunice/30847_CAM043490_d.CR2  30847_CAM043490_d.CR2   
1  images/Eresia eunice/35854_CAM044114_v.JPG  35854_CAM044114_v.JPG   
2  images/Eresia eunice/36158_CAM044195_v.JPG  36158_CAM044195_v.JPG   
3  images/Eresia eunice/30849_CAM043490_v.CR2  30849_CAM043490_v.CR2   
4  images/Eresia eunice/36157_CAM044195_v.CR2  36157_CAM044195_v.CR2   

                                md5  
0  d8827750eebd70652d3e5fb9e3957bfa  
1  46a4abed9e88709b10a0257fc1d89e59  
2  a61633734b2478de40e5f554c266b700  
3  c998c4d5b5cadcd788f7847c3bdd9aec  
4  4876c7e954e6990a5541be6a2cea32a1

In [12]:
def get_filename(image_path):
    return image_path.split("/")[1]

error_df["filename"] = error_df["Image"].apply(get_filename)

In [13]:
missing_filenames = []

for filename in list(error_df.filename.unique()):
    if filename not in list(checksums.filename.unique()):
        missing_filenames.append(filename)

len(missing_filenames)

2666

In [14]:
def get_camid(filename):
    return filename.split("_")[1]

checksums["CAMID"] = checksums["filename"].apply(get_camid)

In [15]:
def get_view(filename):
    if "v" in filename:
        return "ventral"
    elif "d" in filename:
        return "dorsal"
    else:
        return "unknown"

checksums["view"] = checksums["filename"].apply(get_view)
checksums.view.value_counts()

view
dorsal     20955
ventral    20880
unknown      308
Name: count, dtype: int64

In [16]:
error_df["view"] = error_df["filename"].apply(get_view)
error_df.view.value_counts()

view
dorsal     1334
ventral    1332
Name: count, dtype: int64

In [17]:
missing_camids = []
missing_sides = []

for id in list(error_df.CAMID.unique()):
    if id not in list(checksums.CAMID.unique()):
        missing_camids.append(id)
    else:
        checksums_temp_views = (checksums.loc[checksums["CAMID"] == id, "view"].unique())
        error_temp_views = list(error_df.loc[error_df["CAMID"] == id, "view"].unique())
        for view in error_temp_views:
            if view not in checksums_temp_views:
                missing_sides.append(id + "_" + view)

print(f"We have {len(missing_camids)} missing CAMIDs")
print(f"We have {len(missing_sides)} missing sides among CAMIDs that are included")

We have 23 missing CAMIDs
We have 0 missing sides among CAMIDs that are included


In [31]:
missing_camids

['CAM028501',
 'CAM028502',
 'CAM028503',
 'CAM028504',
 'CAM028505',
 'CAM028506',
 'CAM028507',
 'CAM028508',
 'CAM028509',
 'CAM028510',
 'CAM028511',
 'CAM028512',
 'CAM028513',
 'CAM028514',
 'CAM028515',
 'CAM028516',
 'CAM028517',
 'CAM028518',
 'CAM028519',
 'CAM028520',
 'CAM028521',
 'CAM028522',
 'CAM028523']

None of these appear to be in [record 4287444](https://zenodo.org/records/4287444)...Let's see if they're in the master file under any other records...

In [18]:
master = pd.read_csv("../metadata/Jiggins_Zenodo_Img_Master_3477891Patch.csv", low_memory = False)

In [19]:
missing_cam_master = master.loc[master["CAMID"].isin(missing_camids)]
missing_cam_master = missing_cam_master.loc[missing_cam_master.duplicated("CAMID", keep = "first")]

missing_cam_master["record_number"].value_counts()

record_number
4289223    24
Name: count, dtype: int64

In [20]:
# how are there 24??
for camid in list(missing_cam_master.CAMID):
    if camid not in missing_camids:
        print(camid)

for camid in missing_camids:
    if camid not in list(missing_cam_master.CAMID):
        print("missing not in master", camid)

In [38]:
missing_cam_master

CAMID      X      Image_name     View  \
24195  CAM028501  14971  CAM028501d.JPG   dorsal   
24197  CAM028502  14974  CAM028502v.JPG  ventral   
24199  CAM028503  14976  CAM028503v.JPG  ventral   
24201  CAM028504  14978  CAM028504v.JPG  ventral   
24203  CAM028505  14979  CAM028505d.JPG   dorsal   
24205  CAM028506  14982  CAM028506v.JPG  ventral   
24207  CAM028507  14984  CAM028507v.JPG  ventral   
24209  CAM028508  14986  CAM028508v.JPG  ventral   
24211  CAM028509  14988  CAM028509v.JPG  ventral   
24213  CAM028510  14990  CAM028510v.JPG  ventral   
24215  CAM028511  14991  CAM028511d.JPG   dorsal   
24217  CAM028512  14993  CAM028512d.JPG   dorsal   
24219  CAM028513  14997  CAM028513v.JPG  ventral   
24220  CAM028513  14995  CAM028513d.JPG   dorsal   
24222  CAM028514  14998  CAM028514d.JPG   dorsal   
24224  CAM028515  15000  CAM028515d.JPG   dorsal   
24226  CAM028516  15003  CAM028516v.JPG  ventral   
24228  CAM028517  15005  CAM028517v.JPG  ventral   
24230  CAM028518  15006  CAM028518d.JPG   dorsal   
24232  CAM028519  15008  CAM028519d.JPG   dorsal   
24234  CAM028520  15011  CAM028520v.JPG  ventral   
24236  CAM028521  15012  CAM028521d.JPG   dorsal   
24238  CAM028522  15015  CAM028522v.JPG  ventral   
24240  CAM028523  15016  CAM028523d.JPG   dorsal   

                             zenodo_name                        zenodo_link  \
24195  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24197  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24199  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24201  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24203  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24205  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24207  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24209  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24211  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24213  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24215  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24217  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24219  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24220  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24222  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24224  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24226  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24228  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24230  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24232  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24234  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24236  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24238  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24240  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   

      Sequence                      Taxonomic_Name                Locality  \
24195   28,501   Heliconius melpomene ssp. malleti              Río Pusuno   
24197   28,502   Heliconius melpomene ssp. malleti              Río Pusuno   
24199   28,503  Heliconius melpomene ssp. plesseni              Huaymayaco   
24201   28,504  Heliconius melpomene ssp. plesseni              Huaymayaco   
24203   28,505  Heliconius melpomene ssp. plesseni              Huaymayaco   
24205   28,506     Heliconius erato ssp. notabilis              Huaymayaco   
24207   28,507   Heliconius timareta ssp. timareta              Huaymayaco   
24209   28,508  Heliconius melpomene ssp. plesseni              Huaymayaco   
24211   28,509  Heliconius melpo

somehow `CAM028513` was duplicated...

In [40]:
missing_cam_master.loc[missing_cam_master["CAMID"] == "CAM028513"]

CAMID      X      Image_name     View  \
24219  CAM028513  14997  CAM028513v.JPG  ventral   
24220  CAM028513  14995  CAM028513d.JPG   dorsal   

                             zenodo_name                        zenodo_link  \
24219  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   
24220  0.2.rachel.blow.mel.tim.ikiam.csv  https://zenodo.org/record/4289223   

      Sequence                      Taxonomic_Name    Locality  \
24219   28,513  Heliconius melpomene ssp. plesseni  Huaymayaco   
24220   28,513  Heliconius melpomene ssp. plesseni  Huaymayaco   

      Sample_accession  ... Stage   Sex Unit_Type file_type record_number  \
24219              NaN  ...   NaN  Male      Wild       jpg       4289223   
24220              NaN  ...   NaN  Male      Wild       jpg       4289223   

                    species subspecies       genus  \
24219  Heliconius melpomene   plesseni  Heliconius   
24220  Heliconius melpomene   plesseni  Heliconius   

                                                file_url hybrid_stat  
24219  https://zenodo.org/record/4289223/files/CAM028...  non-hybrid  
24220  https://zenodo.org/record/4289223/files/CAM028...  non-hybrid  

[2 rows x 28 columns]

Was this record recorded in the record 3477891 patch file? David said that file resolved many of his failed downloads.


## Pull in record 3477891 multimedia file

Need to run some functions to get more info from columns

In [21]:
import numpy as np

In [22]:
media_rec_3477891 = pd.read_csv("../metadata/deduplication/Zenodo_meta_files/multimedia__(rec_3477891).csv", low_memory=False)

def get_link_filename(identifier):
    if "zenodo" not in identifier:
        link_list = identifier.split("com/")
        link_list[0] = np.nan
    else:
        link_list = identifier.split("/files/")
    # link is first part, filename at end
    return pd.Series(link_list)

def get_record_number(zenodo_link):
    if type(zenodo_link) != float:
        link = zenodo_link.split("record/")
        return link[1]

media_rec_3477891[["zenodo_link", "Image_name"]] = media_rec_3477891["identifier"].apply(get_link_filename)
media_rec_3477891["record_number"] = media_rec_3477891["zenodo_link"].apply(get_record_number)

def get_camid(image_name):
    if "_" in image_name:
        return image_name.split("_")[0]
    else:
        # We have at least one record with image name that doesn't have CAMID (the non-zenodo record)
        return np.nan

media_rec_3477891["CAMID"] = media_rec_3477891["Image_name"].apply(get_camid)
media_rec_3477891["record_number"].value_counts()

record_number
2707828    1276
2714333    1113
2686762     986
2684906     863
2677821     703
2702457     276
2682458     158
2682669     124
2552371      91
2550097      50
2553977      22
2813153      20
Name: count, dtype: int64

In [23]:
for record_num in list(error_df.record_number.unique()):
    if record_num in list(media_rec_3477891.record_number.unique()):
        print(f"{record_num} is in the multimedia file from record 3477891")

2813153 is in the multimedia file from record 477891


In [43]:
media_rec_3477891.loc[media_rec_3477891["record_number"] == "2813153"].shape

(20, 8)

In [48]:
cam = error_df.loc[error_df["record_number"] == "2813153", "CAMID"].values[0]
media_rec_3477891.loc[(media_rec_3477891["record_number"] == "2813153") & (media_rec_3477891["CAMID"] == cam)]

Empty DataFrame
Columns: [coreid, type, identifier, license, zenodo_link, Image_name, record_number, CAMID]
Index: []

In [50]:
print(cam)
media_rec_3477891.loc[media_rec_3477891["CAMID"] == cam]

CAM041882


Empty DataFrame
Columns: [coreid, type, identifier, license, zenodo_link, Image_name, record_number, CAMID]
Index: []

Looks like that `CAMID` isn't in the extra file, so no recovery there.

Record numbers (and their number of images) that had 404 errors:
```
record_number
4287444    2600
4289223      47
4288250       7
5561246       6
3082688       3
1748277       2
2813153       1
```
The one record number covered only had 1 entry.

Let's check by `CAMID`.

In [25]:
media_rec_3477891.loc[media_rec_3477891["CAMID"].isin(missing_camids)]

Empty DataFrame
Columns: [coreid, type, identifier, license, zenodo_link, Image_name, record_number, CAMID]
Index: []

Check for `CAMID`s of any of the images in the error list.

In [26]:
media_rec_3477891.loc[media_rec_3477891["CAMID"].isin(list(error_df["CAMID"].unique()))]


Empty DataFrame
Columns: [coreid, type, identifier, license, zenodo_link, Image_name, record_number, CAMID]
Index: []

Nope, these images seem to be missing...

Should check that the images listed in the master file line up with those in the `batch2.Peru.image.names.csv`.

There were 3924 images listed in that file, with 880 unique IDs. There are 2600 download errors listed for this record (record 4287444), with 579 unique CAMIDs. If we reduce the master file to just entries from this record, we have 

In [27]:
master.loc[master["record_number"] == 4287444].shape, master.loc[master["record_number"] == 4287444].nunique()

((3788, 28),
 CAMID                848
 X                   3788
 Image_name          3788
 View                   6
 zenodo_name            1
 zenodo_link            1
 Sequence             848
 Taxonomic_Name        84
 Locality             112
 Sample_accession       0
 Collected_by           0
 Other_ID             848
 Date                  13
 Dataset                1
 Store                 13
 Brood                  0
 Death_Date             0
 Cross_Type             0
 Stage                  0
 Sex                    0
 Unit_Type              0
 file_type              2
 record_number          1
 species               84
 subspecies             0
 genus                 46
 file_url            3788
 hybrid_stat            0
 dtype: int64)

Master file has less images than suggested by the CSV from the record, and suggests we successfully downloaded 1188 images covering 269 unique IDs.

This matches expectations (see below)

## Check on Succsessful Downloads

In [32]:
LOG_PATH = "../metadata/deduplication/Jiggins_Zenodo_Img_Master_3477891Patch_log_(readable).json"

with open(LOG_PATH, "r") as log_file:
    logs = json.loads(log_file.read())

log_df = pd.DataFrame(data = logs)
log_df.head()

Image  \
0   Greta annette/9290_CAM008455_d.JPG   
1  Greta annette/46076_CAM008455_d.JPG   
2     Greta nero/46078_CAM008456_v.JPG   
3     Greta nero/46077_CAM008456_d.JPG   
4      Greta nero/9291_CAM008456_d.JPG   

                                            file_url record_number  \
0  https://zenodo.org/record/2684906/files/CAM008...       2684906   
1  https://zenodo.org/record/2684906/files/CAM008...       3477891   
2  https://zenodo.org/record/2684906/files/CAM008...       3477891   
3  https://zenodo.org/record/2684906/files/CAM008...       3477891   
4  https://zenodo.org/record/2684906/files/CAM008...       2684906   

                                             dataset      CAMID  \
0  Heliconiine Butterfly Collection Records from ...  CAM008455   
1  Heliconiine Butterfly Collection Records from ...  CAM008455   
2  Heliconiine Butterfly Collection Records from ...  CAM008456   
3  Heliconiine Butterfly Collection Records from ...  CAM008456   
4  Heliconiine Butterfly Collection Records from ...  CAM008456   

  Response_status  
0             200  
1             200  
2             200  
3             200  
4             200

In [33]:
log_df.info(show_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 33846 entries, 0 to 33845
Data columns (total 6 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Image            33846 non-null  object
 1   file_url         33846 non-null  object
 2   record_number    33846 non-null  object
 3   dataset          26627 non-null  object
 4   CAMID            33846 non-null  object
 5   Response_status  33846 non-null  object
dtypes: object(6)
memory usage: 1.5+ MB


In [34]:
log_df.nunique()

Image              33846
file_url           29917
record_number         25
dataset                6
CAMID               9115
Response_status        1
dtype: int64

In [36]:
log_df.loc[log_df["record_number"] == "4287444"].nunique()

Image              1188
file_url           1188
record_number         1
dataset               1
CAMID               269
Response_status       1
dtype: int64

In [38]:
log_df.loc[log_df["record_number"] == "4287444"].sample(5)

Image  \
27729  Pyrrhogyra otolais/32012_CAM043820_d.JPG   
27053    Rhetus periander/31301_CAM043629_v.CR2   
26944    Morpho helenor/31191_CAM043603_hwd.CR2   
27124      Eunica pusilla/31381_CAM043650_v.CR2   
26833     Temenis laothoe/31066_CAM043567_v.JPG   

                                                file_url record_number  \
27729  https://zenodo.org/record/4287444/files/CAM043...       4287444   
27053  https://zenodo.org/record/4287444/files/CAM043...       4287444   
26944  https://zenodo.org/record/4287444/files/CAM043...       4287444   
27124  https://zenodo.org/record/4287444/files/CAM043...       4287444   
26833  https://zenodo.org/record/4287444/files/CAM043...       4287444   

                                                 dataset      CAMID  \
27729  Heliconiine Butterfly Collection Records from ...  CAM043820   
27053  Heliconiine Butterfly Collection Records from ...  CAM043629   
26944  Heliconiine Butterfly Collection Records from ...  CAM043603   
27124  Heliconiine Butterfly Collection Records from ...  CAM043650   
26833  Heliconiine Butterfly Collection Records from ...  CAM043567   

      Response_status  
27729             200  
27053             200  
26944             200  
27124             200  
26833             200

In [41]:
master.loc[master["record_number"] == 4287444, "Dataset"].value_counts()

Dataset
Heliconiine Butterfly Collection Records from University of Cambridge    3228
Name: count, dtype: int64

This is the name on [records 3477891](https://zenodo.org/records/3477891), not record 4287444.

### Save Error Record as CSV

We'll save the error record as a CSV in case of future efforts, but re-alignment seems unlikely. We'll keep only the master file records that were successfully downloaded (still the vast majority).

In [51]:
error_df.to_csv("../metadata/deduplication/Jiggins_Zenodo_Img_Master_3477891Patch_error_log.csv", index = False)